In [93]:
import math
import numpy as np
import plotly.graph_objects as go
import plotly.express as px

In [94]:
def apply_vectorized(functions: list[callable], array: np.array):
    result = np.zeros(array.shape[0], dtype=float)
    for i, f in enumerate(functions):
        result[i] = f(array[i])
    return result

In [95]:
apply_vectorized = np.vectorize(lambda f, x: f(x), otypes=[object])

given 3 neurons, defs:

In [96]:
x = lambda t: 1 / t
weights = np.array([[-0.2,  -1, -0.8], 
                    [   1, 0.8, -1.5], 
                    [ 0.5, 0.6, -0.4]], dtype=float)
initial_weigths = np.array([0.5, 0, -0.5], dtype=float)
activation_functions = [
    lambda h: math.tanh(h),
    lambda h: math.tanh(h),
    lambda h: math.exp(-h*h/2)
    ]
Y = np.array([0.1, 0.1, 0.1], dtype=float)
T = 100


In [103]:
def syncPropagation(weights, initial_weigths, activation_functions, x, t, Y):
    return apply_vectorized(activation_functions, weights.dot(Y.copy()) + initial_weigths * x(t))

In [107]:
def syncPropagation(weights, initial_weigths, activation_functions, x, t, Y):
    nextY = Y.copy()
    h = np.zeros((3))
    for i in range(weights.shape[0]):
        for j in range(weights[i].shape[0]):
            h[i] += Y[j] * weights[i][j]
        h += initial_weigths[i]*x(t)
    nextY = apply_vectorized(activation_functions, h)
    return nextY

In [108]:
def asyncPropagation(weights, initial_weigths, activation_functions, x, t, Y):
    nextY = Y.copy()
    h = np.zeros((3))
    for i in range(weights.shape[0]):
        for j in range(weights[i].shape[0]):
            h[i] += nextY[j] * weights[i][j]
        h += initial_weigths[i]*x(t)
    nextY = apply_vectorized(activation_functions, h)
    return nextY

In [112]:
Ys = np.zeros((T, 3))

ts = np.linspace(0, T, T)
for i, t in enumerate(ts):
    if i == 0:
        Ys[i] = Y.copy()
    else:
        Ys[i] = syncPropagation(weights, initial_weigths, activation_functions, x, t, Ys[i - 1])

Yst = Ys.transpose()
fig = go.Figure()
for i in range(Ys.shape[1]):
    fig.add_trace(go.Scatter(x = ts, y = Yst[i], name = f'Neuron {i}'))
fig.show()


In [113]:
Ys = np.zeros((T, 3))

ts = np.linspace(0, T, T)
for i, t in enumerate(ts):
    if i == 0:
        Ys[i] = Y.copy()
    else:
        Ys[i] = asyncPropagation(weights, initial_weigths, activation_functions, x, t, Ys[i - 1])

Yst = Ys.transpose()
fig = go.Figure()
for i in range(Ys.shape[1]):
    fig.add_trace(go.Scatter(x = ts, y = Yst[i], name = f'Neuron {i}'))
fig.show()

In [59]:

Ys = []
Ys.append(Y.copy())

start = time.perf_counter()

for t in range(1, T+1):
    Y = syncPropagation(weights, initial_weigths, activation_functions, x, t, Y)
    Ys.append(Y.copy())

print(time.perf_counter() - start)

ts = np.linspace(1, T, T)

Ys = np.array(Ys)

fig = go.Figure()
for i in range(Ys.shape[1]):
    fig.add_trace(go.Scatter(x = ts, y = Ys[:, i], name = 'Neuron №' + str(i)))
fig.show()


[[-0.2 -1.  -0.8]
 [ 1.   0.8 -1.5]
 [ 0.5  0.6 -0.4]] [ 0.5  0.  -0.5] [<function <lambda> at 0x00000193CABDB790>, <function <lambda> at 0x00000193CABBECA0>, <function <lambda> at 0x00000193CABBED30>] <function <lambda> at 0x00000193CABBEC10> 1 [0.25722954254804486 -0.9261148139875975 0.7644744142932782]
[[-0.2 -1.  -0.8]
 [ 1.   0.8 -1.5]
 [ 0.5  0.6 -0.4]] [ 0.5  0.  -0.5] [<function <lambda> at 0x00000193CABDB790>, <function <lambda> at 0x00000193CABBECA0>, <function <lambda> at 0x00000193CABBED30>] <function <lambda> at 0x00000193CABBEC10> 2 [0.6428930626884033 -0.9261148143338631 0.4676888663129925]
[[-0.2 -1.  -0.8]
 [ 1.   0.8 -1.5]
 [ 0.5  0.6 -0.4]] [ 0.5  0.  -0.5] [<function <lambda> at 0x00000193CABDB790>, <function <lambda> at 0x00000193CABBECA0>, <function <lambda> at 0x00000193CABBED30>] <function <lambda> at 0x00000193CABBEC10> 3 [0.5872021933068722 -0.6637751005004733 0.7982603849621152]
[[-0.2 -1.  -0.8]
 [ 1.   0.8 -1.5]
 [ 0.5  0.6 -0.4]] [ 0.5  0.  -0.5] [<functio